In [1]:
import pandas as pd
import numpy as np
import pickle
import os
from xgboost import XGBClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import StratifiedGroupKFold
from sklearn.model_selection import GroupKFold, GroupShuffleSplit
from sklearn.feature_selection import SelectKBest, f_classif
from sklearn.metrics import (accuracy_score, precision_score, recall_score, f1_score,
                        roc_curve, auc, roc_auc_score, log_loss)
from sklearn.metrics import classification_report, confusion_matrix, ConfusionMatrixDisplay, accuracy_score, roc_auc_score
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import LabelEncoder
import matplotlib.pyplot as plt
from sklearn.model_selection import LeaveOneOut
from essentials import complete_preprocessing_pipeline
import copy
from sklearn.preprocessing import StandardScaler
import pandas as pd
import numpy as np
from typing import Tuple, Dict
from essentials import normalization
from feature_sets_center_less import GenerateFeatures
# from two_class_ncv_selectk_init import run_modified_nested_cv
from two_class_ncv_selectk import ModifiedNestedCVOptimizer


/home/edumaba/Public/MPhil_Thesis/Code/wear_uropatch/.venv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [ ]:
with open('../data/df_dict_imu.pkl', 'rb') as f:
    imu_dict = pickle.load(f)
with open('../data/df_dict_urineestimate_method1.pkl', 'rb') as f:
    urine_estimates_dict = pickle.load(f)
with open('../data/df_minze_dict.pkl', 'rb') as f:
    ground_truth_dict = pickle.load(f)

In [ ]:
del imu_dict['subj_9_void4']
del imu_dict['subj_11_void2']

In [ ]:
data_dict = copy.deepcopy(imu_dict)
labelled_imu_dict = complete_preprocessing_pipeline(data_dict, ground_truth_dict, 
                                target_fs=60,normalize_data=False, use_three_classes=False)

In [ ]:
# Add experiment_id to each dataframe and append to imu_dict
imu_list = []
for i, key in enumerate(labelled_imu_dict.keys()):
    df  = labelled_imu_dict[key]
    df['experiment_id'] = i + 1

    imu_list.append(df)

In [ ]:
# Concatenate all the dataframes in imu_dict into a single dataframe
main_df = pd.concat(imu_list, ignore_index=True)

In [ ]:
# Define window configurations (same as your pipeline)
window_configs = [
    (1, 0.0), (1, 0.5), (1, 0.8),
    (2, 0.0), (2, 0.5), (2, 0.8),
    (3, 0.0), (3, 0.5), (3, 0.8),
    (4, 0.0), (4, 0.5), (4, 0.8),
    (5, 0.0), (5, 0.5), (5, 0.8)
]

def dataframe_to_dict_by_experiment(df: pd.DataFrame) -> dict:
    """Convert DataFrame to dictionary with experiment_id as key"""
    experiment_dict = {}
    for exp_id in df['experiment_id'].unique():
        exp_data = df[df['experiment_id'] == exp_id].copy()
        exp_data = exp_data.drop(columns=['experiment_id'])
        # IMPORTANT: Reset index to avoid KeyError in feature extraction
        exp_data = exp_data.reset_index(drop=True)
        experiment_dict[f'exp_{exp_id}'] = exp_data
    return experiment_dict

def extract_features_from_dict(data_dict: dict, window_size: float, overlap: float) -> pd.DataFrame:
    """Extract features from dictionary of DataFrames"""
    all_features = []
    
    for exp_key, df in data_dict.items():
        actual_exp_id = int(exp_key.split('_')[1])
        
        analyzer = GenerateFeatures(fs=60, window_duration=window_size, overlap=overlap)
        features, _ = analyzer.analyze_multi_axis_imu(df)
        
        table = analyzer.create_summary_table()
        table['experiment_id'] = actual_exp_id
        all_features.append(table)
    
    return pd.concat(all_features, ignore_index=True)


In [ ]:
# Store results for all window configurations
all_global_norm_results = {}

In [ ]:
n_outer_splits = 5
n_inner_splits = 3

outer_cv = StratifiedGroupKFold(n_splits=n_outer_splits, shuffle=True, random_state=42)
inner_cv = StratifiedGroupKFold(n_splits=n_inner_splits, shuffle=True, random_state=42)

# Loop through each window configuration
for window_size, overlap in window_configs:
    print(f"\n{'='*80}")
    print(f"PROCESSING: {window_size}s window, {overlap} overlap")
    print(f"{'='*80}")
    
    config_fold_results = []

    # Split dictionary into training and testing sets based on void instances
    for fold_id, (train_id, test_id) in enumerate(outer_cv.split(main_df, y=main_df['label'], groups=main_df['experiment_id'])):
        print(f"Fold {fold_id + 1}")
        data_train, data_test = main_df.iloc[train_id], main_df.iloc[test_id]
        _, _ = main_df['label'].iloc[train_id], main_df['label'].iloc[test_id]
        groups_train, groups_test = main_df['experiment_id'].iloc[train_id], main_df['experiment_id'].iloc[test_id]

        
        # Apply global normalization
        data_train_norm, data_test_norm = normalization(data_train, data_test)

        print(f"✓ Applied global normalization")
        print(f"Train experiments: {sorted(groups_train.unique())}")
        print(f"Test experiments: {sorted(groups_test.unique())}")
    
        # Convert normalized DataFrames to dictionaries for feature extraction
        train_dict = dataframe_to_dict_by_experiment(data_train_norm)
        test_dict = dataframe_to_dict_by_experiment(data_test_norm)
        
        # Extract features
        print(f"Extracting features...")
        train_features = extract_features_from_dict(train_dict, window_size, overlap)
        test_features = extract_features_from_dict(test_dict, window_size, overlap)
        
        print(f"Train features shape: {train_features.shape}")
        print(f"Test features shape: {test_features.shape}")
        
        # Store this fold's results
        fold_result = {
            'fold': fold_id + 1,
            'window_size': window_size,
            'overlap': overlap,
            'train_features': train_features,
            'test_features': test_features,
            'original_train_groups': groups_train,
            'original_test_groups': groups_test
        }
        config_fold_results.append(fold_result)
        
    # Store results for this configuration - for each window size and overlap, we get 5 fold results
    overlap_str = 'no' if overlap == 0.0 else str(overlap)
    config_key = f"{window_size}s_{overlap_str}"
    all_global_norm_results[config_key] = config_fold_results
    
    print(f"\n✓ Completed {config_key}: {len(config_fold_results)} folds")
    
print(f"\n{'='*80}")
print("FEATURE EXTRACTION COMPLETED FOR ALL CONFIGURATIONS")
print(f"{'='*80}")

# Show summary
for config_key, fold_results in all_global_norm_results.items():
    print(f"\n{config_key}:")
    for fold_result in fold_results:
        fold_id = fold_result['fold']
        train_shape = fold_result['train_features'].shape
        test_shape = fold_result['test_features'].shape
        print(f"  Fold {fold_result['fold']}: Train{train_shape}, Test{test_shape}")
        
        # Save train and test features to CSV for inspection
        fold_result['train_features'].to_csv(
            f'/home/edumaba/Public/MPhil_Thesis/Code/wear_uropatch/global_normalization/extracted_features/train_{config_key}_fold{fold_id}.csv', 
            index=False
        )
        fold_result['test_features'].to_csv(
            f'/home/edumaba/Public/MPhil_Thesis/Code/wear_uropatch/global_normalization/extracted_features/test_{config_key}_fold{fold_id}.csv', 
            index=False
        )
        


# Nested CV with pre-split data - save each dataset separately

In [2]:
# open pickled results
with open('/home/edumaba/Public/MPhil_Thesis/Code/wear_uropatch/global_normalization/two_class_global_norm_extracted_features.pkl', 'rb') as f:
    all_global_norm_results = pickle.load(f)

In [3]:
# Usage example and convenience function
def run_global_norm_nested_cv_with_class(all_global_norm_results: Dict, base_save_path: str, 
                                        positive_class: str = "void", n_inner_folds: int = 3, 
                                        n_trials: int = 50) -> ModifiedNestedCVOptimizer:
    """
    Convenience function to run global normalization nested CV using the class-based approach.
    
    Parameters:
    -----------
    all_global_norm_results : Dict
        Results from your global normalization pipeline
    base_save_path : str
        Directory to save results
    positive_class : str
        Positive class label
    n_inner_folds : int
        Number of inner CV folds for hyperparameter optimization
    n_trials : int
        Number of optimization trials per model
        
    Returns:
    --------
    ModifiedNestedCVOptimizer instance with all results
    """
    
    # Initialize the optimizer
    optimizer = ModifiedNestedCVOptimizer(
        positive_class=positive_class,
        n_inner_folds=n_inner_folds,
        n_trials=n_trials,
        random_state=42
    )
    
    # Run all configurations
    all_results = optimizer.run_all_configurations(all_global_norm_results, base_save_path)
    
    # Print summary
    best_config, best_model, best_f1 = optimizer.get_best_configuration()
    print(f"\nBEST OVERALL RESULT:")
    print(f"Configuration: {best_config}")
    print(f"Model: {best_model}")
    print(f"F1 Score (positive class): {best_f1:.4f}")
    
    return optimizer


In [4]:
# Simple usage in your notebook:
base_save_path = '/home/edumaba/Public/MPhil_Thesis/Code/wear_uropatch/global_normalization/nested_cv_results/two_class'

# Run everything with one function call
optimizer = run_global_norm_nested_cv_with_class(
    all_global_norm_results,
    base_save_path,
    positive_class="void",
    n_inner_folds=3,
    n_trials=50
)

# Then analyze results easily:
best_config, best_model, best_f1 = optimizer.get_best_configuration()
print(f"Best: {best_config} with {best_model} - F1: {best_f1:.4f}")

# Compare specific configurations
# comparison = optimizer.compare_configurations(['1s_0.5', '2s_0.5', '3s_0.5'])
comparison = optimizer.compare_configurations(['1s_0.5', '2s_0.5', '3s_0.5','3s', '5s_0.5','4s_0.5', '1s', '2s','4s','5s', '1s_0.8', '2s_0.8', '3s_0.8', '4s_0.8', '5s_0.8'])
print(comparison)

# Get detailed summary for best configuration
summary = optimizer.get_configuration_summary(best_config)
print(summary)

[I 2025-09-21 21:45:50,527] A new study created in memory with name: no-name-d8639989-85da-4df6-ba0b-4306b833af6a



GLOBAL NORMALIZATION NESTED CV - CLASS-BASED APPROACH
Base save path: /home/edumaba/Public/MPhil_Thesis/Code/wear_uropatch/global_normalization/nested_cv_results/two_class
Configurations to process: 15

PROCESSING CONFIGURATION: 1s_no

=== DEBUG evaluate_single_fold ===
Fold data keys: ['fold', 'window_size', 'overlap', 'train_features', 'test_features', 'original_train_groups', 'original_test_groups']
Train features shape: (1782, 107)
Train features columns: ['center_time', 'start_time', 'end_time', 'acc_x_permutation_entropy', 'acc_x_spectral_entropy', 'acc_x_mean', 'acc_x_std', 'acc_x_range', 'acc_x_rms', 'acc_x_min', 'acc_x_max', 'acc_x_time_energy', 'acc_x_spectral_centroid', 'acc_x_spectral_spread', 'acc_x_spectral_flatness', 'acc_x_peak_frequency_ratio', 'acc_x_hjorth_frequency', 'acc_x_spectral_skewness', 'acc_x_spectral_kurtosis', 'acc_x_snr', 'acc_y_permutation_entropy', 'acc_y_spectral_entropy', 'acc_y_mean', 'acc_y_std', 'acc_y_range', 'acc_y_rms', 'acc_y_min', 'acc_y_max'

[I 2025-09-21 21:45:51,821] Trial 0 finished with value: -0.5923715354682245 and parameters: {'selector__k': 21, 'selector__score_func': 'f_classif', 'clf__n_estimators': 369, 'clf__max_depth': 3, 'clf__min_samples_split': 20, 'clf__min_samples_leaf': 9, 'clf__max_features': 'sqrt', 'clf__bootstrap': False, 'clf__class_weight': None}. Best is trial 0 with value: -0.5923715354682245.
[I 2025-09-21 21:45:52,204] Trial 1 finished with value: -0.5676007678554215 and parameters: {'selector__k': 73, 'selector__score_func': 'f_classif', 'clf__n_estimators': 70, 'clf__max_depth': 13, 'clf__min_samples_split': 5, 'clf__min_samples_leaf': 1, 'clf__max_features': 'log2', 'clf__bootstrap': True, 'clf__class_weight': None}. Best is trial 1 with value: -0.5676007678554215.
[I 2025-09-21 21:45:54,418] Trial 2 finished with value: -4.3552087304099425 and parameters: {'selector__k': 42, 'selector__score_func': 'f_classif', 'clf__n_estimators': 133, 'clf__max_depth': 20, 'clf__min_samples_split': 16, 'c

      Features selected: 105/105
      Acc: 0.7614, F1(+): 0.6334
    Optimizing XGB...


[I 2025-09-21 21:47:40,924] Trial 0 finished with value: -0.7053099007607689 and parameters: {'selector__k': 21, 'selector__score_func': 'f_classif', 'clf__n_estimators': 369, 'clf__max_depth': 3, 'clf__learning_rate': 0.2708160864249968, 'clf__subsample': 0.9329770563201687, 'clf__colsample_bytree': 0.6849356442713105, 'clf__min_child_weight': 2, 'clf__gamma': 0.9170225492671691, 'clf__reg_alpha': 0.6084844859190754, 'clf__reg_lambda': 1.0495128632644757}. Best is trial 0 with value: -0.7053099007607689.
[I 2025-09-21 21:47:43,141] Trial 1 finished with value: -0.5155419848866748 and parameters: {'selector__k': 94, 'selector__score_func': 'f_classif', 'clf__n_estimators': 281, 'clf__max_depth': 8, 'clf__learning_rate': 0.011711509955524094, 'clf__subsample': 0.8430179407605753, 'clf__colsample_bytree': 0.6682096494749166, 'clf__min_child_weight': 1, 'clf__gamma': 4.7444276862666666, 'clf__reg_alpha': 1.9312640661491187, 'clf__reg_lambda': 1.6167946962329223}. Best is trial 1 with valu

...

      Features selected: 73/105
      Acc: 0.8552, F1(+): 0.8526
    Optimizing XGB...


[I 2025-09-22 01:18:02,246] Trial 0 finished with value: -0.7448906633700898 and parameters: {'selector__k': 21, 'selector__score_func': 'f_classif', 'clf__n_estimators': 369, 'clf__max_depth': 3, 'clf__learning_rate': 0.2708160864249968, 'clf__subsample': 0.9329770563201687, 'clf__colsample_bytree': 0.6849356442713105, 'clf__min_child_weight': 2, 'clf__gamma': 0.9170225492671691, 'clf__reg_alpha': 0.6084844859190754, 'clf__reg_lambda': 1.0495128632644757}. Best is trial 0 with value: -0.7448906633700898.
[I 2025-09-22 01:18:04,090] Trial 1 finished with value: -0.5573728975498025 and parameters: {'selector__k': 94, 'selector__score_func': 'f_classif', 'clf__n_estimators': 281, 'clf__max_depth': 8, 'clf__learning_rate': 0.011711509955524094, 'clf__subsample': 0.8430179407605753, 'clf__colsample_bytree': 0.6682096494749166, 'clf__min_child_weight': 1, 'clf__gamma': 4.7444276862666666, 'clf__reg_alpha': 1.9312640661491187, 'clf__reg_lambda': 1.6167946962329223}. Best is trial 1 with valu

      Features selected: 94/105
      Acc: 0.8043, F1(+): 0.7881
    Optimizing DT...


[I 2025-09-22 01:18:46,354] Trial 4 finished with value: -6.666851812176656 and parameters: {'selector__k': 52, 'selector__score_func': 'f_classif', 'clf__criterion': 'entropy', 'clf__max_depth': 10, 'clf__min_samples_split': 11, 'clf__min_samples_leaf': 5, 'clf__max_features': 'log2', 'clf__splitter': 'best', 'clf__class_weight': 'balanced'}. Best is trial 1 with value: -0.7549964385473692.
[I 2025-09-22 01:18:46,593] Trial 5 finished with value: -7.579563436848534 and parameters: {'selector__k': 94, 'selector__score_func': 'f_classif', 'clf__criterion': 'entropy', 'clf__max_depth': 17, 'clf__min_samples_split': 5, 'clf__min_samples_leaf': 9, 'clf__max_features': None, 'clf__splitter': 'best', 'clf__class_weight': 'balanced'}. Best is trial 1 with value: -0.7549964385473692.
[I 2025-09-22 01:18:46,641] Trial 6 finished with value: -6.602414263414559 and parameters: {'selector__k': 'all', 'selector__score_func': 'f_classif', 'clf__criterion': 'entropy', 'clf__max_depth': 15, 'clf__min_

      Features selected: 73/105
      Acc: 0.5988, F1(+): 0.7117

=== DEBUG _create_exact_format_dataframe ===
Results length: 15
Sample result keys: ['Model', 'Fold', 'Accuracy', 'Precision_Macro', 'Recall_Macro', 'F1_Macro', 'Precision_Weighted', 'Recall_Weighted', 'F1_Weighted', 'Precision_Positive', 'Recall_Positive', 'F1_Positive', 'Precision_Negative', 'Recall_Negative', 'F1_Negative', 'Features_K', 'Score_Function', 'Best_Params', 'HP_selector__k', 'HP_selector__score_func', 'HP_clf__n_estimators', 'HP_clf__max_depth', 'HP_clf__min_samples_split', 'HP_clf__min_samples_leaf', 'HP_clf__max_features', 'HP_clf__bootstrap', 'HP_clf__class_weight']
Sample result: {'Model': 'RF', 'Fold': 1, 'Accuracy': 0.7793, 'Precision_Macro': 0.754, 'Recall_Macro': 0.7565, 'F1_Macro': 0.7552, 'Precision_Weighted': 0.7804, 'Recall_Weighted': 0.7793, 'F1_Weighted': 0.7798, 'Precision_Positive': 0.6716, 'Recall_Positive': 0.6853, 'F1_Positive': 0.6784, 'Precision_Negative': 0.8364, 'Recall_Negative': 0